# GOAL: Test how fast can IP run

#### Upload necessary libraries

In [73]:
import getpass
import pandas as pd
import numpy as np
# import matplotlib as mplot
import urllib.parse
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from IPython.display import Markdown as md
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
import pandas as pd
import plotly.express as px
import pytz

# Extra import
import copy
import random
import gurobipy as gp
from gurobipy import GRB

## To install guroby on Python I used "python -m pip install gurobipy"

pd.set_option('display.max_columns', None)

## PART 1: download and prepare the data

#### Connection

In [74]:
# Input creditials by code (need to remove your private info before you pushed it)
# edm_address = ""
# edm_name = ""
# edm_password = ""

# User input the creditials manually 
edm_address = 'sandpit-edm.awesense.com'
edm_name = 'PIMS-Marco'
edm_password = getpass.getpass(prompt='Password: ')

edm_password = urllib.parse.quote(edm_password)

%load_ext sql
%sql postgresql://$edm_name:$edm_password@$edm_address/edm
%config SqlMagic.displaycon = False
%config SqlMagic.feedback = False

# Delete the credential variables for security purposes.

del edm_name, edm_password

The sql extension is already loaded. To reload it, use:
  %reload_ext sql


Exception during reset or similar
Traceback (most recent call last):
  File "/Users/marcocaoduro/Documents/GitLab/edm-app-examples/directory/lib/python3.10/site-packages/sqlalchemy/pool/base.py", line 739, in _finalize_fairy
    fairy._reset(pool)
  File "/Users/marcocaoduro/Documents/GitLab/edm-app-examples/directory/lib/python3.10/site-packages/sqlalchemy/pool/base.py", line 988, in _reset
    pool._dialect.do_rollback(self)
  File "/Users/marcocaoduro/Documents/GitLab/edm-app-examples/directory/lib/python3.10/site-packages/sqlalchemy/engine/default.py", line 682, in do_rollback
    dbapi_connection.rollback()
psycopg2.OperationalError: server closed the connection unexpectedly
	This probably means the server terminated abnormally
	before or while processing the request.



#### Select parameters

In [75]:
# grid_id = 'awefice'
grid_id = 'North Central Zone'
# grid_element_id = 'transformer_2'
grid_element_id = '12373_hvmv'

#### Create Temporary Views

In [76]:
%%sql 

CREATE OR REPLACE TEMPORARY VIEW grid_element_metric AS
    SELECT grid_id,
            grid_element_id,
            phases,
            type,
            provider,
            direction,
            friendly_id,
            metric_key AS metric,
            valid,
            timestamp,
            value
    FROM grid_element_data_source AS geds
    JOIN UNNEST(geds.metrics::TEXT[]) AS metric_key
        ON true
    LEFT JOIN ts_data_source_select(grid_element_data_source_id, metric_key) AS ts
        ON true;

[]

In [77]:
%%sql

CREATE OR REPLACE TEMPORARY VIEW meter_data_source2 AS
    SELECT meter.grid_id,
            meter.grid_element_id,
            geds.grid_element_data_source_id,
            geds.friendly_id,
            geds.phases,
            geds.provider,
            metric_key as metric,
            lower(geds.valid) as start_time,
            upper(geds.valid) as end_time
    FROM grid_get_downstream('{grid_id}', '{grid_element_id}') AS meter
    LEFT JOIN grid_element_data_source AS geds
        ON meter.grid_element_id = geds.grid_element_id
        AND meter.grid_id = geds.grid_id
        AND geds.type = 'CONSUMER'
    JOIN UNNEST(geds.metrics::TEXT[]) AS metric_key
        ON true
    WHERE meter.type = 'Meter';

[]

In [78]:
%%sql

CREATE OR REPLACE TEMPORARY VIEW meter_consumption2 AS
    SELECT meter.grid_id,
           meter.grid_element_id,
           meter.phases,
           timestamp,
           value AS kWh
    FROM meter_data_source2 AS meter
    LEFT JOIN grid_element_metric AS gem
        ON gem.grid_id = meter.grid_id
        AND gem.grid_element_id = meter.grid_element_id
    WHERE gem.metric = 'kWh'
    AND gem.type = 'CONSUMER';

[]

#### Download data

In [79]:
query = """
SELECT grid_element_id, phases, timestamp, kwh
FROM meter_consumption2
WHERE timestamp >= '2023-01-01 00:00:00'
AND timestamp <= '2023-12-31 23:59:59';
"""

# Execute the query using %sql magic command.
result = %sql $query

meter_consumption_2023_df = result.DataFrame()

#### Add a column with the cluster_id

In [81]:
element_downstream = %sql SELECT grid_element_id, phases, terminal1_cn, terminal2_cn FROM grid_get_downstream('{grid_id}', '{grid_element_id}')
element_downstream = element_downstream.DataFrame()
print('Element_downstream')
print(element_downstream.head())

#Merging elements that come one following the other
BB = element_downstream.merge(element_downstream, left_on='terminal2_cn', right_on='terminal1_cn',suffixes=('_upper', '_lower'))

#Tracing elements where the phases change from ABC to non-ABC
bif = BB[(BB['phases_upper']=='ABC') & (BB['phases_lower']!='ABC')]

meters_under_junctions = pd.DataFrame(columns=['grid_element_id', 'junction'])

#Finding meters under each junction
for junction in bif['grid_element_id_lower']:
    # Find meters under each junction
    meters_under_junction = %sql SELECT grid_element_id FROM grid_get_downstream('{grid_id}', '{junction}')\
                            WHERE type='Meter';
    #     
    meters_under_junction = meters_under_junction.DataFrame()
    meters_under_junction['junction'] = junction
    #
    meters_under_junctions = pd.concat([meters_under_junctions, meters_under_junction], axis=0)

meter_consumption_2023_df = meter_consumption_2023_df.merge(meters_under_junctions, on='grid_element_id')
print(meter_consumption_2023_df.head())

Element_downstream
  grid_element_id phases    terminal1_cn terminal2_cn
0            1001      B   VCN.L17-57801     VCN.1001
1           10017      A   VCN.L17-58401    VCN.10017
2           10102      C  VCN.L17-138949    VCN.10102
3           10157      A       VCN.46765    VCN.10157
4           10159      A      VCN.120807    VCN.10159
  grid_element_id phases                 timestamp       kwh   junction
0        17AY10-1      B 2023-01-01 00:00:00+00:00  1.255925  L17-57719
1        17AY10-1      B 2023-01-01 01:00:00+00:00  2.051644  L17-57719
2        17AY10-1      B 2023-01-01 02:00:00+00:00  1.567479  L17-57719
3        17AY10-1      B 2023-01-01 03:00:00+00:00  1.903236  L17-57719
4        17AY10-1      B 2023-01-01 04:00:00+00:00  1.600963  L17-57719


#### Aggregate the clusters

In [83]:
#grouping power consumption each junction
meter_consumption_2023_df.groupby(['junction','phases', 'timestamp']).agg({'kwh': 'sum'}).reset_index()

meter_consumption_2023_df

junction phases                 timestamp       kwh
0          104479      A 2023-01-01 00:00:00+00:00  1.679400
1          104479      A 2023-01-01 01:00:00+00:00  1.988358
2          104479      A 2023-01-01 02:00:00+00:00  1.311260
3          104479      A 2023-01-01 03:00:00+00:00  1.494376
4          104479      A 2023-01-01 04:00:00+00:00  1.384515
...           ...    ...                       ...       ...
350395  L17-84944      B 2023-12-31 19:00:00+00:00  5.773608
350396  L17-84944      B 2023-12-31 20:00:00+00:00  4.996740
350397  L17-84944      B 2023-12-31 21:00:00+00:00  4.668996
350398  L17-84944      B 2023-12-31 22:00:00+00:00  6.206254
350399  L17-84944      B 2023-12-31 23:00:00+00:00  4.597096

[350400 rows x 4 columns]

#### Plot of the aggregate consumption on the three phases

In [87]:
initial_aggregation = meter_consumption_2023_df.groupby(['phases', 'timestamp'])['kwh'].sum().reset_index()

# Plot graph
px.line(initial_aggregation, x='timestamp', y='kwh', color='phases', title='Aggregate consumption per phase over 2023')


/Users/marcocaoduro/Documents/GitLab/edm-app-examples/directory/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



#### Compute average aggregation

In [116]:
average_aggregation = meter_consumption_2023_df.groupby(['timestamp'])['kwh'].sum().reset_index()
average_aggregation = average_aggregation.set_index('timestamp')
average_aggregation = average_aggregation / 3
print(average_aggregation.head())
print(average_aggregation.loc['2023-01-01 00:00:00+00:00'].values[0])

                                  kwh
timestamp                            
2023-01-01 00:00:00+00:00  263.078478
2023-01-01 01:00:00+00:00  271.221868
2023-01-01 02:00:00+00:00  241.423854
2023-01-01 03:00:00+00:00  264.196307
2023-01-01 04:00:00+00:00  246.188703
263.0784779056963


#### Compute the initial sum of the imbalances

In [104]:
initial_imbalance= []
# A
initial_A_aggregation = meter_consumption_2023_df[meter_consumption_2023_df['phases'] == 'A'].groupby(['timestamp'])['kwh'].sum().reset_index()
initial_A_aggregation = initial_A_aggregation.set_index('timestamp')
# B
initial_B_aggregation = meter_consumption_2023_df[meter_consumption_2023_df['phases'] == 'B'].groupby(['timestamp'])['kwh'].sum().reset_index()
initial_B_aggregation = initial_B_aggregation.set_index('timestamp')
# C
initial_C_aggregation = meter_consumption_2023_df[meter_consumption_2023_df['phases'] == 'C'].groupby(['timestamp'])['kwh'].sum().reset_index()
initial_C_aggregation = initial_C_aggregation.set_index('timestamp')
#
for t in meter_consumption_2023_df.timestamp.unique():
    dev_A = abs( initial_A_aggregation.loc[t].kwh - average_aggregation.loc[t].kwh )
    dev_B = abs( initial_B_aggregation.loc[t].kwh - average_aggregation.loc[t].kwh )
    dev_C = abs( initial_C_aggregation.loc[t].kwh - average_aggregation.loc[t].kwh )
    max_deviation = max([dev_A, dev_B, dev_C])
    imbalance = (max_deviation * 100) / average_aggregation.loc[t].kwh
    initial_imbalance.append([t, imbalance])
initial_imbalance = pd.DataFrame(initial_imbalance, columns = ['timestamp','imbalance'])
initial_imbalance = initial_imbalance.set_index('timestamp')
print( initial_imbalance.head())
initial_sum_of_imbalance = sum(initial_imbalance.imbalance)
print(initial_sum_of_imbalance )

                           imbalance
timestamp                           
2023-01-01 00:00:00+00:00  65.660693
2023-01-01 01:00:00+00:00  63.105362
2023-01-01 02:00:00+00:00  60.762473
2023-01-01 03:00:00+00:00  62.543098
2023-01-01 04:00:00+00:00  60.391928
550223.4109722943


#### Create a dictionary of junctions

In [106]:
junctions= {}
for junction_name in meter_consumption_2023_df.junction.unique():
    # Extract the data of a meter
    junc = meter_consumption_2023_df[(meter_consumption_2023_df['junction'] == junction_name)]
    # Identify the current phase of the meter
    current_phase = junc.iloc[0].phases
    # Remove the columns that are not used
    junc = junc[['timestamp', 'kwh']]
    # Set 'timestamp' as the index of the DataFrame
    junc = junc.set_index('timestamp')
    junctions[junction_name] = [junc, current_phase]
print(junctions['L17-136410'])


[                                kwh
timestamp                          
2023-01-01 00:00:00+00:00  6.667671
2023-01-01 01:00:00+00:00  6.415954
2023-01-01 02:00:00+00:00  5.939568
2023-01-01 03:00:00+00:00  6.250243
2023-01-01 04:00:00+00:00  5.837372
...                             ...
2023-12-31 19:00:00+00:00  7.139909
2023-12-31 20:00:00+00:00  5.717551
2023-12-31 21:00:00+00:00  5.071090
2023-12-31 22:00:00+00:00  7.545171
2023-12-31 23:00:00+00:00  4.983045

[8760 rows x 1 columns], 'A']


## PART 2: Integer Programming Model

#### Define iterators and constant

In [107]:
junctions_id = meter_consumption_2023_df.junction.unique()
times = meter_consumption_2023_df.timestamp.unique()
phases = meter_consumption_2023_df.phases.unique()
max_changes = 5
#
# Compute the initial sum of the max_diff


#### Define model and variables

In [108]:
# Create Model
m = gp.Model('Optimize_Over_Month')

# Creare Variables
x = m.addVars(junctions_id, phases, name = 'active_phase_junction', vtype = GRB.BINARY)
change = m.addVars(junctions_id, name = 'is_there_a_change_in_the_junction', vtype = GRB.BINARY)
aggregate = m.addVars(times, phases, name = 'aggregate_consumption_per_phase')
max_diff = m.addVars(times, name = 'max_deviation_per_unit_time')
phase_imbalance = m.addVars(times, name = 'phase_imbalance_per_unit_time')

#### Define Easy Constrains

In [109]:
# Create Constraints
# -- Only one phase can be assigned to a junction
one_phase_per_junction = m.addConstrs((gp.quicksum(x[id,p] for p in phases) == 1 for id in junctions_id))
#
# -- Detect change at each meter 
is_junction_changed = m.addConstrs(change[j] == gp.quicksum((1 - int( p == junctions[j][1] ))*x[j,p] for p in phases) for j in junctions_id)
#
# -- Limit the number of possible changes
limit_changes = m.addConstr(gp.quicksum(change[j] for j in junctions_id) <= max_changes)

#### Define "tricky" Constrains

In [119]:
# -- Compute the phase imbalance at each time
aggregate_consumptions = m.addConstrs(aggregate[t, p] == gp.quicksum(x[j,p]*junctions[j][0].loc[t].values[0] for j in junctions_id) for t in times for p in phases)
max_deviation_1 = m.addConstrs(max_diff[t] >=  (aggregate[t, p] - average_aggregation.loc[t].values[0]) for t in times for p in phases)
max_deviation_2 = m.addConstrs(max_diff[t] >= -(aggregate[t, p] - average_aggregation.loc[t].values[0]) for t in times for p in phases)
# Note that since it is a Linear Model, we cannot normalize by dividing by the average
phase_imbalances = m.addConstrs(phase_imbalance[t] == max_diff[t] / average_aggregation.loc[t].values[0] for t in times)

#### Objective Function

In [120]:
#m.setObjective(gp.quicksum(phase_imbalance[mo] for mo in months)) 
m.setObjective(gp.quicksum(phase_imbalance[t] for t in times))

#### Write and solve the IP

In [121]:
# Write LP to check it
m.write("OptimalChanges.lp")

# Let's solve it!
m.optimize()

Gurobi Optimizer version 11.0.2 build v11.0.2rc0 (mac64[rosetta2] - Darwin 23.0.0 23A344)

CPU model: Apple M2
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 192801 rows, 43960 columns and 3460480 nonzeros
Model fingerprint: 0x7720b6cd
Variable types: 43800 continuous, 160 integer (160 binary)
Coefficient statistics:
  Matrix range     [1e-03, 6e+02]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 7e+02]
Presolve removed 113880 rows and 8760 columns
Presolve time: 4.20s
Presolved: 78921 rows, 35200 columns, 1182880 nonzeros
Variable types: 35040 continuous, 160 integer (160 binary)

Deterministic concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Root barrier log...

Ordering time: 0.15s

Barrier statistics:
 Dense cols : 120
 AA' NZ     : 1.235e+06
 Factor NZ  : 5.927e+06 (roughly 100 MB of memory)
 Factor Ops : 5.259e+08 (less than 1 second p

#### Exctract and visualize the solution

In [122]:
# Extract the solution
x_values = pd.Series(m.getAttr("X",x), name = 'phases')
change_values = pd.Series(m.getAttr("X",change), name = 'changes')
IP_changes = []
for j in junctions_id:
    for p in phases:
        val = x_values[j,p]
        if val > 0 and change_values[j] == 1:
            IP_changes.append([j, p])
print(IP_changes)

[['L17-140872', 'A'], ['L17-58026', 'C'], ['L17-58058', 'A'], ['L17-58268', 'A'], ['L17-58281', 'C']]


# PART 3: Check the improvement

#### Apply changes

In [123]:
# Modify Data
new_meter_consumption_2023_df = copy.deepcopy(meter_consumption_2023_df)
for c in IP_changes:
    id_j = c[0]
    phase_j = c[1]
    new_meter_consumption_2023_df.loc[new_meter_consumption_2023_df['junction'] == id_j, 'phases'] = phase_j

#### Check the solution

In [131]:
aggregated_consumption = meter_consumption_2023_df.groupby(['phases', 'timestamp'])['kwh'].sum().reset_index()

# Plot graph
fig_before = px.line(aggregated_consumption, x='timestamp', y='kwh', color='phases', title='Aggregated consumption per phase over 2023 - BEFORE changes')

new_aggregated_consumption = new_meter_consumption_2023_df.groupby(['phases', 'timestamp'])['kwh'].sum().reset_index()

# Plot graph
fig_after = px.line(new_aggregated_consumption, x='timestamp', y='kwh', color='phases', title='Aggregated consumption per phase over 2023 - AFTER changes')

fig_before.show()

fig_after.show()





/Users/marcocaoduro/Documents/GitLab/edm-app-examples/directory/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/Users/marcocaoduro/Documents/GitLab/edm-app-examples/directory/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



#### Compute final imbalance

In [127]:
new_imbalance= []
# A
new_A_aggregation = new_meter_consumption_2023_df[new_meter_consumption_2023_df['phases'] == 'A'].groupby(['timestamp'])['kwh'].sum().reset_index()
new_A_aggregation = new_A_aggregation.set_index('timestamp')
# B
new_B_aggregation = new_meter_consumption_2023_df[new_meter_consumption_2023_df['phases'] == 'B'].groupby(['timestamp'])['kwh'].sum().reset_index()
new_B_aggregation = new_B_aggregation.set_index('timestamp')
# C
new_C_aggregation = new_meter_consumption_2023_df[new_meter_consumption_2023_df['phases'] == 'C'].groupby(['timestamp'])['kwh'].sum().reset_index()
new_C_aggregation = new_C_aggregation.set_index('timestamp')
#
for t in meter_consumption_2023_df.timestamp.unique():
    dev_A = abs( new_A_aggregation.loc[t].kwh - average_aggregation.loc[t].kwh )
    dev_B = abs( new_B_aggregation.loc[t].kwh - average_aggregation.loc[t].kwh )
    dev_C = abs( new_C_aggregation.loc[t].kwh - average_aggregation.loc[t].kwh )
    max_deviation = max([dev_A, dev_B, dev_C])
    imbalance = (max_deviation * 100) / average_aggregation.loc[t].kwh
    new_imbalance.append([t, imbalance])
new_imbalance = pd.DataFrame(new_imbalance, columns = ['timestamp','imbalance'])
new_imbalance = new_imbalance.set_index('timestamp')
print( new_imbalance.head())
new_sum_of_imbalance = sum(new_imbalance.imbalance)
print(new_sum_of_imbalance )

                           imbalance
timestamp                           
2023-01-01 00:00:00+00:00   8.159788
2023-01-01 01:00:00+00:00   2.111017
2023-01-01 02:00:00+00:00   6.595890
2023-01-01 03:00:00+00:00   8.020734
2023-01-01 04:00:00+00:00   0.263034
40588.59201926177


#### Plot the imbalance before and after the changes

In [130]:
fig_imb_before = px.line(initial_imbalance.reset_index(), x='timestamp', y='imbalance', title='Plot of the Imbalances - BEFORE changes')
fig_imb_after = px.line(new_imbalance.reset_index(), x='timestamp', y='imbalance', title='Plot of the Imbalances - AFTER changes')
fig_imb_before.show()
fig_imb_after.show()

/Users/marcocaoduro/Documents/GitLab/edm-app-examples/directory/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/Users/marcocaoduro/Documents/GitLab/edm-app-examples/directory/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

